In [37]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc




def add_layers_anndata(process_type, input_file_h5ad, gene_annot_file, species, SRP_name, resolution, base_folder, ice_type):


    bins_bed = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.csv', names=['chr', 'start', 'end'])
    bins_bed['bin_id'] = bins_bed.index.tolist()

    bins_bed.to_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv', index=False, header=False, sep='\t')
    if species == 'human':

        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Human/hg38-blacklist.v2.bed'
    else:
        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Mouse/mm10-blacklist.v2.bed'

    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {blacklist_file} -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed")
    blacklist_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'c1', 'c2', 'c3', 'c4'])
    
    
    adata = ad.read_h5ad(f'{input_file_h5ad}')

    data = adata.X + 0.0
    
    if resolution == '1kbp_raw':
    
        data = data.astype('float32')
        
    elif resolution == '10kbp_raw':
    
        data = data.astype('float32')
    else:
        data = data.astype('float64')
        
    np_of_rows = len(adata.obs_names.tolist())
    np_of_col = len(adata.var_names.tolist())
        
    

        
    
    nan_columns = blacklist_bins['bin_id'].tolist()

    data[:, nan_columns] = np.nan


    chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()

    chrom_index_list  = {}
    for chrom in chr_list:
          st = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[0]
          en = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[-1]
          chrom_index_list[chrom] = list(range(st, en+1))

    chrom_index_list_intra = {}
    for chrom in chr_list:
        index_list = []
        for chrom2 in chr_list:
            if chrom2 != chrom:
                index_list.extend(chrom_index_list[chrom2])

        chrom_index_list_intra[chrom] = index_list

    gtf = read_gtf(gene_annot_file)
    genes = gtf.df.loc[gtf.df['Feature'] == 'gene'].copy()
    genes['gene_id'] = [x.split('.')[0] for x in genes['gene_id']]
    genes['gene_id'].drop_duplicates(inplace=True)

    if not genes['Chromosome'].str.startswith('chr').any():
        genes['Chromosome'] = [f'chr{x}' for x in genes['Chromosome']]

    genes  = genes.set_index('gene_id')

    genes = genes.loc[adata.obs_names.tolist(), :]
    
    genes = genes.reset_index()



    genes[['Chromosome', 'Start', 'End', 'gene_id']].to_csv(f'{base_folder}hi_c_data_processing/data_{species}/gene_info.tsv', index=False, header=False, sep='\t')


    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {base_folder}hi_c_data_processing/data_{species}/gene_info.tsv -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv")
    gene_id_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'st', 'end', 'gene_id', 'c4'])

    
    if process_type == 'intra':

        layer_value_list = [0, 1, 10, 100, 1000]
        layer_name_list = ['intra']*len(layer_value_list)

    if process_type == 'inter':
        layer_name_list = ['inter']
        layer_value_list = [0]

    if process_type == 'gw':
        layer_value_list = [0, 1, 10, 100, 1000]
        layer_name_list = ['intra']*len(layer_value_list)
        layer_name_list.append('inter')
        layer_value_list.append(0)



    for layer_type, dist in zip(layer_name_list, layer_value_list):
        
            adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
        
            new_layer_name = f'{process_type}_{layer_type}_{dist}'
        
        #if new_layer_name in adata.layers:
        #    continue
        #else:

            mask = np.zeros_like(data, dtype=bool)

        

            for index, row in genes.iterrows():

                if layer_type == 'intra':
                    columns_to_mask = chrom_index_list_intra[row['Chromosome']]
                else:
                    columns_to_mask = chrom_index_list[row['Chromosome']]

                mask[index, columns_to_mask] = True

                if layer_type == 'intra':

                    start_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].min()

                    end_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].max()

                    mask[index, start_index:end_index+1]  = True

                    #for idx in [start_index, end_index]:
                    mask[index, max(0, start_index - dist):min(data.shape[1], end_index + dist+1)] = True




            data_layered = np.where(mask, np.nan, data)



            layer_name = f'{layer_type}_{dist}_raw'

            adata_l.layers[layer_name] = data_layered

            z_scores = stats.zscore(data_layered, axis=1, nan_policy='omit')


            clipped_z_scores = np.clip(z_scores, -10, 10)



            layer_name = f'{layer_type}_{dist}_z_scores'

            adata_l.layers[layer_name] = clipped_z_scores



            del z_scores
            del clipped_z_scores
            gc.collect()

            #data_plus_one = data_layered + 1

            #log_transformed_data = np.log1p(data_plus_one)

            del data_layered
            #del data_plus_one
            gc.collect()

            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed'

            #adata.layers[layer_name] = log_transformed_data

            #z_scores = stats.zscore(log_transformed_data, axis=1, nan_policy='omit')

            #clipped_z_scores = np.clip(z_scores, -10, 10)



            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed_z_scores'

            #adata.layers[layer_name] = clipped_z_scores

            #del z_scores
            #del log_transformed_data
            #del clipped_z_scores
            #gc.collect()
            adata_l.obs_names = adata.obs_names.tolist()
            adata_l.var_names = adata.var_names.tolist()
            
            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{layer_name}_by_allbins_max.h5ad'
            
            

            adata_l.write(outputfile_h5ad, compression="gzip")
            
            

In [ ]:
for species in ['human', 'mouse']:
    for process_type in ['intra', 'inter']:
        for resolution in ['500kbp_raw', '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
            base_folder = '/grid/gillis/data_norepl/lohia/'
            SRP_name='aggregates'
            ice_type='KR'
            input_file_h5ad=f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_by_allbins_max.h5ad'
            if species=='mouse':
                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
            else:
                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
            add_layers_anndata(process_type, input_file_h5ad, gene_annot_file, species, SRP_name, resolution, base_folder, ice_type)





In [ ]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf



from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc

# Assuming your data is organized as NumPy arrays
# gene_observation_matrix is genesXobservations
# gene_category_matrix is genesXcategories
# Both matrices are NumPy arrays

# Example gene_observation_matrix (5 genes, 3 observations) with NaN values


# Calculate the mean of genes for each category and observation, ignoring NaN values
def calculate_category_means_ignore_nan(gene_observation_matrix_df, gene_category_matrix_df):
    # Calculate mean for each category (axis=0) and each observation (axis=1), ignoring NaN values


    genes_intersect = gene_observation_matrix_df.index.intersection(gene_category_matrix_df.index)

    gene_observation_matrix_df =  gene_observation_matrix_df.loc[genes_intersect, :]
    gene_category_matrix_df = gene_category_matrix_df.loc[genes_intersect, :]

    gene_observation_matrix = gene_observation_matrix_df.values
    gene_category_matrix = gene_category_matrix_df.values

    category_counts = np.dot(gene_category_matrix.T, ~np.isnan(gene_observation_matrix))
    
    gene_observation_matrix_cleaned = np.nan_to_num(gene_observation_matrix, nan=0.0)
    
    category_sums = np.dot(gene_category_matrix.T, gene_observation_matrix_cleaned)
    
    # Calculate mean using only non-NaN values
    category_means = category_sums / category_counts
    
    # Replace NaN values in category_means with 0 where division by 0 occurred
    #category_means[np.isnan(category_means)] = 0.0
    
    return category_means, category_counts

# Call the function to calculate category means, ignoring NaN values


def calc_marker_matrix(marker_list,gene_list, no_of_markers=10,  drop_duplicates=True, shuffle_labels=False):
    
        
        marker_list = marker_list[marker_list['Ensembl_gene_identifier'].isin(gene_list)]

        marker_list = marker_list.sort_values(by=['rank']).drop_duplicates(subset=['cell_type', 'gene'])
        
        all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()

        marker_list_list = []
        for group2 in all_cell_types:
                    m_tmp = marker_list[marker_list['cell_type']==group2].sort_values(by=['rank'])
                    m_tmp['rank_missing_gene'] = [x+1 for x in range(m_tmp.shape[0])]

                    marker_list_list.append(m_tmp)

        marker_list = pd.concat(marker_list_list)

        marker_list = marker_list[marker_list['rank_missing_gene']<=no_of_markers]

        marker_list['%recurrence'] = marker_list['recurrence'] / marker_list['n_datasets']
        marker_list['%recurrence'] = 1/marker_list['%recurrence']
        
        marker_list_copy = marker_list.copy()
        

        


        if drop_duplicates==True:

            marker_list = marker_list.sort_values(by=['rank', '%recurrence', 'auroc', 'rank_missing_gene']).drop_duplicates(subset=['Ensembl_gene_identifier'], keep=False)
        elif drop_duplicates=="one_copy":
            marker_list = marker_list.sort_values(by=['rank', '%recurrence', 'auroc', 'rank_missing_gene']).drop_duplicates(subset=['Ensembl_gene_identifier'])
        else:
            pass
        
        if shuffle_labels == True:
            

            shuffled_Ensembl_gene_identifier = marker_list['Ensembl_gene_identifier'].sample(frac=1, replace=False, random_state=42).reset_index(drop=True)


            marker_list['Ensembl_gene_identifier'] = shuffled_Ensembl_gene_identifier.tolist()
            
        else:
            pass


        df2_list = []
        for group2 in all_cell_types:
                    
                    m_tmp = marker_list[marker_list['cell_type']==group2]
                    #if number_of_times == 1:
                    df2_list.append(m_tmp)
                    #else:
                    #    random_indices = np.random.choice(m_tmp.index, size=bootstarp_size, replace=True)
                    #    bootstrap_sample = m_tmp.loc[random_indices]
                    #    df2_list.append(bootstrap_sample)

        marker_list=pd.concat(df2_list)
        marker_list_copy['rank'] = 0
        marker_list = pd.concat([marker_list, marker_list_copy])
        
        

        marker_table = marker_list.pivot_table(index='Ensembl_gene_identifier', columns='cell_type', values='rank', aggfunc='sum')

        marker_table.fillna(0, inplace=True)

        marker_table[marker_table != 0] = 1

        

        return marker_table
        

#for each marker-list and input file , I can make one output file

def calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name):

        marker_list= pd.read_csv(f'{base_folder}/hi_c_data_processing/{species}_{marker_name}.csv')
        cell_type_order = marker_list['cell_type'].drop_duplicates().tolist()



        
        

        adata = ad.read_h5ad(f'{input_file_h5ad}')
        
        np_of_col = adata.X.shape[1]
        np_of_rows = len(cell_type_order)
        
        #adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
        
        layer_names = adata.layers.keys()
        no_of_markers_list = [1,2,3,4,5,6,7,8,9,10,11,12,13,15,17,19,21,23,25,29,33,37,41,46,50,58,65,73,82,92,100,115,129,144,150,162,181,200,227,250,284,300,356,400,446,500]     
        for given_layer in layer_names:
            for drop_duplicates in [False, True]:
                    for shuf in [True, False]:
                        
                        for no_of_markers in no_of_markers_list:
                                adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
                        
                            
                                

                                gene_list = adata.obs_names.tolist()

                                gene_observation_matrix_dataframe = adata.to_df(layer=given_layer)

                                gene_category_dataframe = calc_marker_matrix(marker_list, gene_list, no_of_markers=no_of_markers,  drop_duplicates=drop_duplicates, shuffle_labels=shuf)

                                gene_category_dataframe = gene_category_dataframe.loc[:,cell_type_order]

                                category_means, category_counts = calculate_category_means_ignore_nan(gene_observation_matrix_dataframe, gene_category_dataframe)

                                l_n = f'mean'

                                adata_l.layers[l_n] = category_means

                                l_n = f'counts'

                                adata_l.layers[l_n] = category_counts
                                
                                #z_scores = stats.zscore(category_means, axis=0, nan_policy='omit')
                                #l_n = f'{given_layer}_{no_of_markers}_{drop_duplicates}_{shuf}_mean_scaled'
                                #adata_l.layers[l_n] = z_scores
                                
                                #z_scores = stats.zscore(category_counts, axis=0, nan_policy='omit')
                                #l_n = f'{given_layer}_{no_of_markers}_{drop_duplicates}_{shuf}_counts_scaled'
                                #adata_l.layers[l_n] = z_scores


                                adata_l.obs_names = cell_type_order
                                adata_l.var_names = adata.var_names.tolist()

                                outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_{no_of_markers}_by_allbins_max_mean.h5ad'

                                adata_l.write(outputfile_h5ad, compression="gzip")








In [ ]:

for species in ['human']:
    for process_type in ['inter']:
        for resolution in ['250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
                for marker_name in ['brain_class', 'brain_heart', 'heart']:
                    layer_name = 'z_scores'
                    base_folder = '/grid/gillis/data_norepl/lohia/'
                    SRP_name='aggregates'
                    ice_type='KR'
                    input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                    if species=='mouse':
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                    else:
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                    calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name)



In [ ]:

for species in ['mouse']:
    for process_type in ['inter']:
        for resolution in ['250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
                for marker_name in ['brain_class', 'brain_blood', 'blood']:
                    layer_name = 'z_scores'
                    base_folder = '/grid/gillis/data_norepl/lohia/'
                    SRP_name='aggregates'
                    ice_type='KR'
                    input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                    if species=='mouse':
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                    else:
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                    calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name)


In [ ]:
for species in ['human']:
    for process_type in ['intra']:
        for resolution in ['10kbp_raw']:
            for dist in [0,1,10,100]:
                for marker_name in ['brain_class', 'brain_heart', 'heart']:
                    layer_name = 'z_scores'
                    base_folder = '/grid/gillis/data_norepl/lohia/'
                    SRP_name='aggregates'
                    ice_type='KR'
                    input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                    if species=='mouse':
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                    else:
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                    calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name)

for species in ['mouse']:
    for process_type in ['intra']:
        for resolution in ['10kbp_raw']:
            for dist in [0,1,10,100]:
                for marker_name in ['brain_class', 'brain_blood', 'blood']:
                    layer_name = 'z_scores'
                    base_folder = '/grid/gillis/data_norepl/lohia/'
                    SRP_name='aggregates'
                    ice_type='KR'
                    input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                    if species=='mouse':
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                    else:
                        gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                    calc_mean_profile(marker_name, base_folder, species, input_file_h5ad, process_type,  ice_type, dist, layer_name)

In [17]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc


#egad function

import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck


def run_egad(go, nw, **kwargs):
    """EGAD running function
    
    Wrapper to lower level functions for EGAD

    EGAD measures modularity of gene lists in co-expression networks. 

    This was translated from the MATLAB version, which does tiled Cross Validation
    
    The useful kwargs are:
    int - nFold : Number of CV folds to do, default is 3, 
    int - {min,max}_count : limits for number of terms in each gene list, these are exclusive values


    Arguments:
        go {pd.DataFrame} -- dataframe of genes x terms of values [0,1], where 1 is included in gene lists
        nw {pd.DataFrame} -- dataframe of co-expression network, genes x genes
        **kwargs 
    
    Returns:
        pd.DataFrame -- dataframe of terms x metrics where the metrics are 
        ['AUC', 'AVG_NODE_DEGREE', 'DEGREE_NULL_AUC', 'P_Value']
    """
    assert nw.shape[0] == nw.shape[1] , 'Network is not square'
    assert np.all(nw.index == nw.columns) , 'Network index and columns are not in the same order'
    nw_mask = nw.isna().sum(axis=1) != nw.shape[1]
    #print (nw_mask)
    nw = nw.loc[nw_mask, nw_mask].astype(float)
    #print (nw)
    #np.fill_diagonal(nw.values, 1)
    return _runNV(go, nw, **kwargs)


def _runNV(go, nw, nFold=3, min_count=1, max_count=1000):

    #Make sure genes are same in go and nw
    genes_intersect = go.index.intersection(nw.index)

    go = go.loc[genes_intersect, :]
    nw = nw.loc[genes_intersect, genes_intersect]

    #Make sure there aren't duplicates
    duplicates = nw.index.duplicated(keep='first')
    nw = nw.loc[~duplicates, ~duplicates]

    go = go.loc[:, (go.sum(axis=0) > min_count) & (go.sum(axis=0) < max_count)]
    go = go.loc[~go.index.duplicated(keep='first'), :]
    
    roc = _new_egad(go.values, nw.values, nFold)

    col_names = ['AUC', 'AVG_NODE_DEGREE', 'DEGREE_NULL_AUC', 'P_Value']
    #Put output in dataframe
    return pd.DataFrame(dict(zip(col_names, roc)), index=go.columns)


def _new_egad(go, nw, nFold):

    #Build Cross validated Positive
    x, y = np.where(go)
    cvgo = {}
    for i in np.arange(nFold):
        a = x[i::nFold]
        b = y[i::nFold]
        dat = np.ones_like(a)
        mask = sparse.coo_matrix((dat, (a, b)), shape=go.shape)
        cvgo[i] = go - mask.toarray()
        
    CVgo = np.concatenate(list(cvgo.values()), axis=1)

    sumin = np.matmul(nw.T, CVgo)

    degree = np.sum(nw, axis=0)

    predicts = sumin / degree[:, None]

    np.place(predicts, CVgo > 0, np.nan)
    


    #Calculate ranks of positives
    #rank_abs = lambda x: stats.rankdata(np.abs(x))
    #predicts2 = np.apply_along_axis(rank_abs, 0, predicts)
    predicts2  = bottleneck.nanrankdata(abs(predicts), axis=0)


    #Masking Nans that were ranked (how tiedrank works in matlab)
    predicts2[np.isnan(predicts)] = np.nan
    


    filtering = np.tile(go, nFold)

    #negatives :filtering == 0
    #Sets Ranks of negatives to 0
    np.place(predicts2, filtering == 0, 0)

    #Sum of ranks for each prediction
    p = bottleneck.nansum(predicts2, axis=0)

    #Number of predictions
    #Number of 1's masked for each GO term for each CV
    n_p = np.sum(filtering, axis=0) - np.sum(CVgo, axis=0)

    #Number of negatives
    #Number of GO terms - number of postiive
    n_n = filtering.shape[0] - np.sum(filtering, axis=0)

    roc = (p / n_p - (n_p + 1) / 2) / n_n
    U = roc * n_p * n_n
    Z = (np.abs(U - (n_p * n_n / 2))) / np.sqrt(n_p * n_n *
                                                (n_p + n_n + 1) / 12)
    roc = roc.reshape(nFold, go.shape[1])
    Z = Z.reshape(nFold, go.shape[1])
    #Stouffer Z method
    Z = bottleneck.nansum(Z, axis=0) / np.sqrt(nFold)
    #Calc ROC of Neighbor Voting
    roc = bottleneck.nanmean(roc, axis=0)
    P = stats.norm.sf(Z)

    #Average degree for nodes in each go term
    avg_degree = degree.dot(go) / np.sum(go, axis=0)

    #Calc null auc for degree
    ranks = np.tile(stats.rankdata(degree), (go.shape[1], 1)).T

    np.place(ranks, go == 0, 0)

    n_p = bottleneck.nansum(go, axis=0)
    nn = go.shape[0] - n_p
    p = bottleneck.nansum(ranks, axis=0)

    roc_null = (p / n_p - ((n_p + 1) / 2)) / nn

    return roc, avg_degree, roc_null, P


tissue_dict = {'Chandelier': "brain",
 'Lamp5': "brain",
 'Lamp5_Lhx6': "brain",
 'Pax6': "brain",
 'Pvalb': "brain",
 'Sncg': "brain",
 'Sst': "brain",
 'Chandelier': "brain",
 'Sst Chodl': "brain",
 'Meis2': "brain",
 'Vip': "brain",
 'L2/3 IT': "brain",
 'L4 IT': "brain",
 'L5 ET': "brain",
 'L5 IT': "brain",
 'L5 PT': "brain",
 'L4/5 IT': "brain",
 'L5/6 NP': "brain",
 'L6 CT': "brain",
 'L6 IT': "brain",
 'L6 IT Car3': "brain",
 'L6b': "brain",
 'Astro': 'brain',
 'Endo': 'brain',
 'Micro-PVM': 'brain',
 'OPC': 'brain',
 'Oligo': "brain",
 'VLMC':'brain', 
 'Peri': 'brain',
 'SMC': 'brain',
 'T cell': 'heart',
 'basophil': 'heart',
 'erythroblast': 'heart',
 'granulocyte': 'heart',
 'hematopoietic precursor cell': 'heart',
 'immature B cell': 'heart',
 'immature natural killer cell': 'heart',
 'late pro-B cell': 'heart',
 'macrophage': 'heart',
 'monocyte': 'heart',
 'naive B cell': 'heart',
 'pro-B cell': 'heart',
 'proerythroblast' : 'heart',
 'Adipocytes' : 'heart',
 'Cardiomyocytes': 'heart',
 'Endocardial': 'heart',
 'Endothelial_Arterial': 'heart' ,
 'Endothelial_Capillaries': 'heart',
 'Endothelial_Other': 'heart',
 'Endothelial_Venous': 'heart',
 'Fibroblasts': 'heart',
 'Pericytes_Stromal': 'heart',
 'Smooth_Muscle_Cells': 'heart',
 'Pericytes': 'heart',
 'Epicardium_FB-like': 'heart',
 'Epicardium_Meso': 'heart',
 'Epicardium_Proliferating': 'heart',
 'Immature_Cardiomyocytes': 'heart',
 'Immature_other': 'heart',
 'Lymphoid_Immune_Cells': 'heart',
 'Myeloid_Immune_Cells': 'heart',
 'Neuronal_Cells': 'heart',}


NvsNN_dict = {'Chandelier': "N",
 'Lamp5': "N",
 'Lamp5_Lhx6': "N",
 'Pax6': "N",
 'Pvalb': "N",
 'Sncg': "N",
 'Sst': "N",
 'Chandelier': "N",
 'Sst Chodl': "N",
 'Meis2': "N",
 'Vip': "N",
 'L2/3 IT': "N",
 'L4 IT': "N",
 'L5 ET': "N",
 'L5 IT': "N",
 'L5 PT': "N",
 'L4/5 IT': "N",
 'L5/6 NP': "N",
 'L6 CT': "N",
 'L6 IT': "N",
 'L6 IT Car3': "N",
 'L6b': "N",
 'Astro': 'NN',
 'Endo': 'NN',
 'Micro-PVM': 'NN',
 'OPC': 'NN',
 'Oligo': "NN",
 'VLMC':'NN', 
 'Peri': 'NN',
 'SMC': 'NN',
}

GlutvsGaba_dict = {'Chandelier': "Gaba",
 'Lamp5': "Gaba",
 'Lamp5_Lhx6': "Gaba",
 'Pax6': "Gaba",
 'Pvalb': "Gaba",
 'Sncg': "Gaba",
 'Sst': "Gaba",
 'Chandelier': "Gaba",
 'Sst Chodl': "Gaba",
 'Meis2': "Gaba",
 'Vip': "Gaba",
 'L2/3 IT': "Glut",
 'L4 IT': "Glut",
 'L5 ET': "Glut",
 'L5 IT': "Glut",
 'L5 PT': "Glut",
 'L4/5 IT': "Glut",
 'L5/6 NP': "Glut",
 'L6 CT': "Glut",
 'L6 IT': "Glut",
 'L6 IT Car3': "Glut",
 'L6b': "Glut",
 }


def create_dict_from_columns(name_age_dict):
    # Create a dictionary from two columns of the DataFrame

    given_dict = name_age_dict.copy()
    
    n = len(given_dict.keys())
    tp_class = np.zeros((n, n))

    # Fill the diagonal elements with 1
    np.fill_diagonal(tp_class, 1)

    df_tp_class = pd.DataFrame(tp_class, index=given_dict.keys(), columns=given_dict.values())

    # Update the DataFrame based on the given_dict
    for key, value in given_dict.items():
        df_tp_class.loc[key, value] = 1

    # Remove duplicate columns
    df_tp_class = df_tp_class.loc[:, ~df_tp_class.columns.duplicated()]
    
    return df_tp_class

# Calculate the mean of genes for each category and observation, ignoring NaN values
def calculate_pearson_correlation(df_a, corr_method):
    # Calculate mean for each category (axis=0) and each observation (axis=1), ignoring NaN values


    df_corr = df_a.T.corr(min_periods=200, method=corr_method)
     
    return df_corr

# Call the function to calculate category means, ignoring NaN values



        

#for each marker-list and input file , I can make one output file

def calc_egad_vals(input_file_h5ad, outputfile_h5ad):

        

        adata = ad.read_h5ad(f'{input_file_h5ad}')
        
        np_of_col = len(adata.obs_names.tolist())
        np_of_rows = len(adata.obs_names.tolist())
        
        adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))
        
        layer_names = adata.layers.keys()    
        for corr_method in ['pearson']:
                        for given_layer in layer_names:



                                df_a = adata.to_df(layer=given_layer)

                                df_corr = calculate_pearson_correlation(df_a, corr_method)

                                l_n = f'{given_layer}_{corr_method}'

                                adata_l.layers[l_n] = df_corr

                                df_corr  = df_corr.fillna(0)
                                
                                df_corr += abs(df_corr.min().min())
                                
                                print (df_corr)

                                #df_list  = []
                                
                                if marker_name == 'brain_class':
                                    name_age_dict =  NvsNN_dict.copy()
                                    class_name = ['NvsNN']
                                else:
                                    name_age_dict =  tissue_dict.copy()
                                    class_name = 'tissue'

                                #for name_age_dict, class_name in zip([tissue_dict , NvsNN_dict], ['tissue' , 'NvsNN']):

                                df_tp_class = create_dict_from_columns(name_age_dict)

                                df_exp = run_egad(df_tp_class, df_corr)

                                #    df_list.append(df_exp)
                                #df_exp = pd.concat(df_list)

                                adata_l.uns[l_n] = df_exp



        adata_l.obs_names = adata.obs_names.tolist()
        adata_l.var_names = adata.obs_names.tolist()

        adata_l.write(outputfile_h5ad, compression="gzip")



In [19]:




for species in ['mouse']:
    for process_type in ['intra', 'inter']:
        for resolution in ['500kbp_raw', '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
            for shuf in [True, False]:
                for drop_duplicates in [True, False]:
                    for marker_name in ['brain_class', 'brain_blood']:
                        dist = 0
                        layer_name = 'z_scores'
                        base_folder = '/grid/gillis/data_norepl/lohia/'
                        SRP_name='aggregates'
                        ice_type='KR'
                        input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                        if species=='mouse':
                            gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                        else:
                            gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                        input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'
                        outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_egad.h5ad'
                        calc_egad_vals(input_file_h5ad, outputfile_h5ad)


for species in ['human']:
    for process_type in ['intra', 'inter']:
        for resolution in ['500kbp_raw', '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
            for shuf in [True, False]:
                for drop_duplicates in [True, False]:
                    for marker_name in ['brain_class', 'brain_heart']:
                        dist = 0
                        layer_name = 'z_scores'
                        base_folder = '/grid/gillis/data_norepl/lohia/'
                        SRP_name='aggregates'
                        ice_type='KR'
                        input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                        if species=='mouse':
                            gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                        else:
                            gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
                        input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'
                        outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_egad.h5ad'
                        calc_egad_vals(input_file_h5ad, outputfile_h5ad)





            Chandelier  Lamp5_Lhx6       OPC     Lamp5      Pax6      Sncg  \
Chandelier    1.230704    0.320294  0.306941  0.238806  0.655569  0.578067   
Lamp5_Lhx6    0.320294    1.230704  0.754262  0.489551  0.345114  0.480718   
OPC           0.306941    0.754262  1.230704  0.709323  0.622727  0.694581   
Lamp5         0.238806    0.489551  0.709323  1.230704  0.717515  0.380667   
Pax6          0.655569    0.345114  0.622727  0.717515  1.230704  0.358799   
Sncg          0.578067    0.480718  0.694581  0.380667  0.358799  1.230704   
L4 IT         0.307838    0.433834  0.727610  0.322191  0.359397  0.563839   
L5 IT         0.435386    0.340138  0.719423  0.302308  0.667279  0.650601   
Pvalb         0.558730    0.216805  0.646702  0.267938  0.526810  0.809150   
L2/3 IT       0.403098    0.645938  0.783467  0.540285  0.188465  0.797221   
L6 IT         0.070081    0.903571  1.005286  0.567197  0.360790  0.678372   
L6 IT Car3    0.640312    0.603509  0.870436  0.454265  0.439427

            Chandelier  Lamp5_Lhx6       OPC     Lamp5      Pax6      Sncg  \
Chandelier    1.407998    0.543548  0.691417  0.597764  0.134631  0.320235   
Lamp5_Lhx6    0.543548    1.407998  1.118573  0.683879  0.394396  0.643661   
OPC           0.691417    1.118573  1.407998  0.530213  0.345124  0.644434   
Lamp5         0.597764    0.683879  0.530213  1.407998  0.647640  0.523640   
Pax6          0.134631    0.394396  0.345124  0.647640  1.407998  0.777691   
Sncg          0.320235    0.643661  0.644434  0.523640  0.777691  1.407998   
L4 IT         0.752976    0.594114  0.468620  0.789052  0.445082  0.901353   
L5 IT         0.612150    0.487894  0.573587  0.643863  0.760766  1.130998   
Pvalb         0.775683    0.397410  0.485356  1.084796  0.565516  0.675453   
L2/3 IT       0.719266    0.444194  0.236682  0.581274  0.093281  0.456146   
L6 IT         0.525710    1.026928  0.730900  0.613784  0.285940  0.743116   
L6 IT Car3    0.740095    0.507450  0.511488  0.596542  0.839387

            Chandelier  Lamp5_Lhx6       OPC     Lamp5      Pax6      Sncg  \
Chandelier    1.253432    0.592155  0.463411  0.714012  0.451912  0.236833   
Lamp5_Lhx6    0.592155    1.253432  0.894565  0.464669  0.370832  0.454999   
OPC           0.463411    0.894565  1.253432  0.422597  0.378923  0.415978   
Lamp5         0.714012    0.464669  0.422597  1.253432  0.443428  0.489855   
Pax6          0.451912    0.370832  0.378923  0.443428  1.253432  0.590037   
Sncg          0.236833    0.454999  0.415978  0.489855  0.590037  1.253432   
L4 IT         0.199718    0.717508  0.772406  0.314160  0.397417  0.396371   
L5 IT         0.767929    0.721678  0.641042  0.486566  0.422849  0.273043   
Pvalb         0.305304    0.400912  0.639198  0.342059  0.472953  0.329454   
L2/3 IT       0.470857    1.077198  1.021016  0.419988  0.184292  0.531107   
L6 IT         0.385341    0.682747  0.478584  0.093198  0.440687  0.415682   
L6 IT Car3    0.524547    0.637028  0.962867  0.278876  0.241693

            Chandelier  Lamp5_Lhx6       OPC     Lamp5      Pax6      Sncg  \
Chandelier    1.135854    0.453581  0.299857  0.441601  0.309830  0.462739   
Lamp5_Lhx6    0.453581    1.135854  0.688038  0.290631  0.391156  0.415865   
OPC           0.299857    0.688038  1.135854  0.233141  0.191959  0.459722   
Lamp5         0.441601    0.290631  0.233141  1.135854  0.297932  0.652069   
Pax6          0.309830    0.391156  0.191959  0.297932  1.135854  0.618516   
Sncg          0.462739    0.415865  0.459722  0.652069  0.618516  1.135854   
L4 IT         0.250180    0.777639  0.737258  0.336199  0.551173  0.454732   
L5 IT         0.709850    0.545243  0.563850  0.347452  0.254275  0.305379   
Pvalb         0.314373    0.458697  0.853557  0.351536  0.329701  0.448173   
L2/3 IT       0.195999    0.872143  0.812628  0.380750  0.342661  0.649377   
L6 IT         0.565764    0.685715  0.527227  0.180481  0.284123  0.470098   
L6 IT Car3    0.402318    0.552938  0.935524  0.221236  0.283001

            Chandelier  Lamp5_Lhx6       OPC     Lamp5      Pax6      Sncg  \
Chandelier    1.405870    0.360072  0.647694  0.454914  0.687921  0.309503   
Lamp5_Lhx6    0.360072    1.405870  1.008412  0.664072  0.517109  0.760617   
OPC           0.647694    1.008412  1.405870  0.651944  1.011077  0.458279   
Lamp5         0.454914    0.664072  0.651944  1.405870  0.333022  0.600046   
Pax6          0.687921    0.517109  1.011077  0.333022  1.405870  0.327655   
Sncg          0.309503    0.760617  0.458279  0.600046  0.327655  1.405870   
L4 IT         0.199864    0.621330  0.521204  0.717947  0.366941  0.721351   
L5 IT         0.304282    0.584040  0.426517  0.852390  0.397685  0.644928   
Pvalb         0.552741    0.633373  0.554948  1.151582  0.333493  0.877700   
L2/3 IT       0.000000    0.446021  0.259006  0.536104  0.340558  0.594450   
L6 IT         0.473119    1.066052  0.932791  0.699338  0.581179  1.025037   
L6 IT Car3    0.505345    0.636037  0.661329  0.956538  0.363642

            Chandelier  Lamp5_Lhx6       OPC     Lamp5      Pax6      Sncg  \
Chandelier    1.271784    0.306299  0.301061  0.241621  0.507106  0.430694   
Lamp5_Lhx6    0.306299    1.271784  0.915958  0.545997  0.556002  0.586101   
OPC           0.301061    0.915958  1.271784  0.477352  0.917254  0.416995   
Lamp5         0.241621    0.545997  0.477352  1.271784  0.344738  0.712671   
Pax6          0.507106    0.556002  0.917254  0.344738  1.271784  0.344732   
Sncg          0.430694    0.586101  0.416995  0.712671  0.344732  1.271784   
L4 IT         0.045650    0.493116  0.622024  0.930387  0.627757  0.626389   
L5 IT         0.473168    0.452007  0.498320  0.621666  0.645339  0.379300   
Pvalb         0.466755    0.500191  0.663399  0.871910  0.364302  0.863458   
L2/3 IT       0.125097    0.354308  0.192721  0.426538  0.328977  0.180120   
L6 IT         0.382381    0.861551  0.948458  0.698647  0.617971  0.837045   
L6 IT Car3    0.310884    0.440994  0.618263  1.000295  0.501260

            Chandelier  Lamp5_Lhx6       OPC     Lamp5      Pax6      Sncg  \
Chandelier    1.209192    0.078488  0.218431  0.088171  0.508754  0.147854   
Lamp5_Lhx6    0.078488    1.209192  0.950885  0.747072  0.551198  0.876979   
OPC           0.218431    0.950885  1.209192  0.472600  0.834189  0.556227   
Lamp5         0.088171    0.747072  0.472600  1.209192  0.250700  0.837050   
Pax6          0.508754    0.551198  0.834189  0.250700  1.209192  0.398464   
Sncg          0.147854    0.876979  0.556227  0.837050  0.398464  1.209192   
L4 IT         0.109194    0.737597  0.602684  0.939450  0.494709  0.718834   
L5 IT         0.485952    0.317879  0.610498  0.338487  0.634574  0.208291   
Pvalb         0.238803    0.496440  0.571152  0.801293  0.409511  0.655704   
L2/3 IT       0.124977    0.351463  0.189089  0.369889  0.410048  0.280713   
L6 IT         0.047319    0.967489  0.863376  0.860263  0.533845  0.960639   
L6 IT Car3    0.213820    0.610661  0.585342  0.860267  0.566495

            Chandelier  Lamp5_Lhx6       OPC     Lamp5      Pax6      Sncg  \
Chandelier    1.232746    0.354499  0.253278  0.436457  0.657594  0.330718   
Lamp5_Lhx6    0.354499    1.232746  0.923056  0.639272  0.474738  0.690670   
OPC           0.253278    0.923056  1.232746  0.781918  0.527097  0.677373   
Lamp5         0.436457    0.639272  0.781918  1.232746  0.094983  0.745702   
Pax6          0.657594    0.474738  0.527097  0.094983  1.232746  0.169461   
Sncg          0.330718    0.690670  0.677373  0.745702  0.169461  1.232746   
L4 IT         0.257040    0.499768  0.737593  0.774685  0.113338  0.739990   
L5 IT         0.387668    0.558343  0.656787  0.500763  0.309537  0.598217   
Pvalb         0.480066    0.236096  0.422658  0.683242  0.295706  0.668429   
L2/3 IT       0.143160    0.725471  0.570227  0.652367  0.010165  0.755193   
L6 IT         0.331439    0.902686  1.107924  0.802665  0.364196  0.862854   
L6 IT Car3    0.620835    0.624190  0.727213  0.760055  0.279573

            Chandelier  Lamp5_Lhx6       OPC     Lamp5      Pax6      Sncg  \
Chandelier    1.268404    0.360372  0.319214  0.468950  0.647819  0.325301   
Lamp5_Lhx6    0.360372    1.268404  0.808217  0.618169  0.342022  0.370316   
OPC           0.319214    0.808217  1.268404  0.732605  0.621658  0.497282   
Lamp5         0.468950    0.618169  0.732605  1.268404  0.403598  0.706855   
Pax6          0.647819    0.342022  0.621658  0.403598  1.268404  0.322208   
Sncg          0.325301    0.370316  0.497282  0.706855  0.322208  1.268404   
L4 IT         0.446663    0.377172  0.757428  0.556622  0.372224  0.681345   
L5 IT         0.443633    0.461408  0.677288  0.418538  0.473490  0.701230   
Pvalb         0.588503    0.191421  0.545054  0.690557  0.414523  0.837682   
L2/3 IT       0.403630    0.714776  0.750054  0.711795  0.000000  0.561423   
L6 IT         0.285249    0.941957  1.033362  0.752548  0.335435  0.627851   
L6 IT Car3    0.387966    0.489170  0.916227  0.408408  0.488680

            Chandelier  Lamp5_Lhx6       OPC     Lamp5      Pax6      Sncg  \
Chandelier    1.425037    0.691681  0.948813  0.845744  0.237267  0.469538   
Lamp5_Lhx6    0.691681    1.425037  0.893059  0.667518  0.421094  0.905302   
OPC           0.948813    0.893059  1.425037  0.845273  0.560925  0.607315   
Lamp5         0.845744    0.667518  0.845273  1.425037  0.545472  0.824570   
Pax6          0.237267    0.421094  0.560925  0.545472  1.425037  0.610259   
Sncg          0.469538    0.905302  0.607315  0.824570  0.610259  1.425037   
L4 IT         0.683277    0.825763  0.730127  1.084064  0.493836  1.114959   
L5 IT         0.741762    0.361491  0.780042  0.974815  0.894885  0.676380   
Pvalb         0.550779    0.778238  0.498517  0.996370  0.305211  0.954411   
L2/3 IT       0.603585    0.417140  0.196039  0.666949  0.160883  0.657165   
L6 IT         0.486934    1.044770  0.662044  0.600504  0.347899  0.824018   
L6 IT Car3    0.743853    0.674686  0.593119  0.863436  0.576502

In [ ]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc


#egad function

import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck




def calculate_pearson_correlation(df, df_b, corr_method):
    # Perform bin intersection
    bins_intersect = set(df.columns.tolist()).intersection(set(df_b.columns.tolist()))
    df = df.loc[:, bins_intersect]
    #df = df.fillna(0)
    #df_b = df_b.fillna(0)
    df_b = df_b.loc[:, bins_intersect]


    # Z-score normalization
    df_b_z = stats.zscore(df_b, axis=0, nan_policy='omit')
    df_b_z = pd.DataFrame(df_b_z, index=df_b.index.tolist(), columns=df_b.columns)
    df_b_z['cell_type'] = df_b_z.index.tolist()
    df_b_z = df_b_z.set_index(['cell_type'])

    df_z = stats.zscore(df, axis=0, nan_policy='omit')
    df_z = pd.DataFrame(df_z, index=df.index.tolist(), columns=df.columns)
    df_z['cell_type'] = df_z.index.tolist()
    df_z['cell_type'] = [x + '_hic' for x in df_z['cell_type']]
    df_z = df_z.set_index(['cell_type'])
    

    # Concatenate dataframes
    #print (df_b_z)
    #print (df_z)
    df_corr = pd.concat([df_b_z, df_z], axis=0)

    
    
    #df_corr = df_corr.dropna(axis=1, how='all')
    #df_corr = df_corr.dropna(axis=1)
    
    #df_corr = df_corr.set_index(['cell_type'])

            
    features_sc = stats.zscore(df_corr, axis=0, nan_policy='omit')
    
    #features_sc = features_sc.dropna(how='all', axis=1).fillna(0)
    
    #features_sc = features_sc.dropna(how='all', axis=1)
    
                
    df_dist_df = features_sc.T.corr(min_periods=10, method=corr_method)



    return df_dist_df


def calculate_auc_nan(df_dist_df, tp):
    df_jac_subset = df_dist_df.values
    df_exp_subset = tp.values

    coodinates_1 = np.where(np.isnan(df_jac_subset))
    coodinates_2 = np.where(np.isnan(df_exp_subset))

    x_coo = coodinates_1[0].tolist() + coodinates_2[0].tolist()
    y_coo = coodinates_1[1].tolist() + coodinates_2[1].tolist()

    df_jac_subset[x_coo, y_coo] = np.nan
    df_exp_subset[x_coo, y_coo] = np.nan

    predicts2 = bottleneck.nanrankdata(df_jac_subset, axis=1)

    tp = df_exp_subset.copy()
    tn = 1 - tp

    pos_rank_sum = tp * predicts2
    auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1))) - (np.nansum(tp, axis=1) + 1) / 2)) / np.nansum(tn, axis=1)

    df_auc = pd.DataFrame({'cell_type': df_dist_df.index.tolist(), 'AUC': auc_array})

    return df_auc

cell_type_map = {
 'Adipocyte' : 'Adipocytes',
 'Atrial Cardiomyocyte': 'Cardiomyocytes',
 'Ventricular Cardiomyocyte':'Immature_Cardiomyocytes',
 'Endothelial_Arterial': 'Endothelial' ,
 'Fibroblast': 'Fibroblasts',
 'Smooth Muscle': 'Smooth_Muscle_Cells',
 'Lymphocyte': 'Lymphoid_Immune_Cells',
 'Macrophage': 'Myeloid_Immune_Cells',
 'Nervous': 'Neuronal_Cells',}
        

#for each marker-list and input file , I can make one output file

def calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name):
    

        adata = ad.read_h5ad(f'{input_file_h5ad}', backed='r')
        adata_b = ad.read_h5ad(f'{input_file_another_exp_h5ad}', backed='r')
        df_b = adata_b.to_df()
        
        if marker_name == 'heart':
            df_b.index = [cell_type_map[x] for x in cell_type_map]

        df = adata.to_df()

        cell_type_intersect = df.index.intersection(df_b.index)


        df_b = df_b.loc[cell_type_intersect,:]
        

        np_of_col = len(cell_type_intersect)*2
        np_of_rows = len(cell_type_intersect)*2
        
        adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))

        
        layer_names = adata.layers.keys()    
        for corr_method in ['pearson']:
                        for given_layer in layer_names:
                        #for given_layer in accepted_layer_list:
                        
                        


                                df = adata.to_df(layer=given_layer)

                                df = df.loc[cell_type_intersect,:]

                                df_corr_real_names = calculate_pearson_correlation(df, df_b, corr_method)

                                l_n = f'{given_layer}_{corr_method}'

                                adata_l.layers[l_n] = df_corr_real_names

                                # Perform cell type intersection
                                #cell_type_intersect = df.index.intersection(df_b.index)

                                hic_cell_type = [x + '_hic' for x in cell_type_intersect]

                                df_corr = df_corr_real_names.loc[cell_type_intersect,:]
                            
                                df_corr = df_corr[hic_cell_type]

                                #df_corr  = df_corr.fillna(0)

                                #df_corr += abs(df_corr.min().min())

                                given_dict = dict(zip(df_corr.index.tolist(), df_corr.index.tolist()))

                                n = len(given_dict.keys())

                                tp_class = np.zeros((n, n))

                                # Fill the diagonal elements with 1
                                np.fill_diagonal(tp_class, 1)

                                df_tp_class = pd.DataFrame(tp_class, index=given_dict.keys(), columns=given_dict.values())

                                for key, value in given_dict.items():
                                    df_tp_class.loc[key, value] = 1
                            
                                df_tp_class = df_tp_class.loc[df_corr.index.tolist(), :]
                                    
                                    
                                df_exp = calculate_auc_nan(df_corr, df_tp_class)

                                adata_l.uns[l_n] = df_exp



        adata_l.obs_names = df_corr_real_names.index.tolist()
        adata_l.var_names = df_corr_real_names.columns.tolist()

        adata_l.write(outputfile_h5ad, compression="gzip")


In [ ]:





for species in ['mouse']:
    for process_type in ['intra']:
        for resolution in ['500kbp_raw', '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
            for shuf in [True, False]:
                for drop_duplicates in [False]:
                    for marker_name in ['brain_class']:
                        for dist in [0,1,10,100]:
                            layer_name = 'z_scores'
                            base_folder = '/grid/gillis/data_norepl/lohia/'
                            SRP_name='aggregates'
                            ice_type='KR'
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                            if species=='mouse':
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                            else:
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'
                            input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_atac.h5ad'


                            calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)
                            
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'                            
                            input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/compartment.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_compartment.h5ad'
                            calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)



for species in ['mouse']:
    for process_type in ['inter']:
        for resolution in ['500kbp_raw', '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
            for shuf in [True, False]:
                for drop_duplicates in [False]:
                    for marker_name in ['brain_class']:
                            dist = 0
                            layer_name = 'z_scores'
                            base_folder = '/grid/gillis/data_norepl/lohia/'
                            SRP_name='aggregates'
                            ice_type='KR'
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                            if species=='mouse':
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                            else:
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'
                            input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_atac.h5ad'


                            calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)
                            
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'                            
                            input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/compartment.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_compartment.h5ad'
                            calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)








for species in ['human']:
    for process_type in ['intra']:
        for resolution in ['500kbp_raw', '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
            for shuf in [True, False]:
                for drop_duplicates in [False]:
                    for marker_name in ['brain_class']:
                        for dist in [0,1,10,100]:
                            layer_name = 'z_scores'
                            base_folder = '/grid/gillis/data_norepl/lohia/'
                            SRP_name='aggregates'
                            ice_type='KR'
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                            if species=='mouse':
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                            else:
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'
                            input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_atac.h5ad'


                            calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)
                            
                            marker_name = 'heart'
                            
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'
                            input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_heart.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_atac.h5ad'


                            calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)
                            
  


for species in ['human']:
    for process_type in ['inter']:
        for resolution in ['500kbp_raw', '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
            for shuf in [True, False]:
                for drop_duplicates in [False]:
                    for marker_name in ['brain_class']:
                            dist = 0
                            layer_name = 'z_scores'
                            base_folder = '/grid/gillis/data_norepl/lohia/'
                            SRP_name='aggregates'
                            ice_type='KR'
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                            if species=='mouse':
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                            else:
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'
                            input_file_another_exp_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/zemke_brain.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_atac.h5ad'


                            calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name)
                            



In [ ]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc


#egad function

import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck




def calculate_pearson_correlation(df, df_b, corr_method):
    # Perform bin intersection
    bins_intersect = set(df.columns.tolist()).intersection(set(df_b.columns.tolist()))
    df = df.loc[:, bins_intersect]
    #df = df.fillna(0)
    #df_b = df_b.fillna(0)
    df_b = df_b.loc[:, bins_intersect]


    # Z-score normalization
    df_b_z = stats.zscore(df_b, axis=0, nan_policy='omit')
    df_b_z = pd.DataFrame(df_b_z, index=df_b.index.tolist(), columns=df_b.columns)
    df_b_z['cell_type'] = df_b_z.index.tolist()
    df_b_z = df_b_z.set_index(['cell_type'])

    df_z = stats.zscore(df, axis=0, nan_policy='omit')
    df_z = pd.DataFrame(df_z, index=df.index.tolist(), columns=df.columns)
    df_z['cell_type'] = df_z.index.tolist()
    df_z['cell_type'] = [x + '_hic' for x in df_z['cell_type']]
    df_z = df_z.set_index(['cell_type'])
    

    # Concatenate dataframes
    df_corr = pd.concat([df_b_z, df_z])

    
    
    #df_corr = df_corr.dropna(axis=1, how='all')
    #df_corr = df_corr.dropna(axis=1)
    
    #df_corr = df_corr.set_index(['cell_type'])

            
    features_sc = stats.zscore(df_corr, axis=0, nan_policy='omit')
    
    #features_sc = features_sc.dropna(how='all', axis=1).fillna(0)
    
    #features_sc = features_sc.dropna(how='all', axis=1)
    
                
    df_dist_df = features_sc.T.corr(min_periods=200, method=corr_method)



    return df_dist_df


def calculate_auc_nan(df_dist_df, tp):
    df_jac_subset = df_dist_df.values
    df_exp_subset = tp.values

    coodinates_1 = np.where(np.isnan(df_jac_subset))
    coodinates_2 = np.where(np.isnan(df_exp_subset))

    x_coo = coodinates_1[0].tolist() + coodinates_2[0].tolist()
    y_coo = coodinates_1[1].tolist() + coodinates_2[1].tolist()

    df_jac_subset[x_coo, y_coo] = np.nan
    df_exp_subset[x_coo, y_coo] = np.nan

    predicts2 = bottleneck.nanrankdata(df_jac_subset, axis=1)

    tp = df_exp_subset.copy()
    tn = 1 - tp

    pos_rank_sum = tp * predicts2
    auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1))) - (np.nansum(tp, axis=1) + 1) / 2)) / np.nansum(tn, axis=1)

    df_auc = pd.DataFrame({'cell_type': df_dist_df.index.tolist(), 'AUC': auc_array})

    return df_auc


        

#for each marker-list and input file , I can make one output file

def calc_pair_corr(input_file_h5ad_a, input_file_h5ad_b, file_b_species, outputfile_h5ad, resolution, base_folder, SRP_name):

        adata = ad.read_h5ad(f'{input_file_h5ad_a}', backed='r')
        adata_b = ad.read_h5ad(f'{input_file_h5ad_b}', backed='r')
        df_b = adata_b.to_df()

        df = adata.to_df()

        cell_type_intersect = df.index.intersection(df_b.index)




        species_input='mouse'
        species_output='human'
        
        if file_b_species == 'mouse':
            species_input='mouse'
            species_output='human'
        else:
            species_input='human'
            species_output='mouse'
        
        full_input_path = f'{base_folder}/hi_c_data_processing/data_{species_input}/{SRP_name}/{resolution}/max/'
        
        full_target_path = f'{base_folder}/hi_c_data_processing/data_{species_output}/{SRP_name}/{resolution}/max/'
        if species_input=='mouse':
            chain_file = 'mm10ToHg38.over.chain.gz'
        else:
            chain_file = 'hg38ToMm10.over.chain.gz'
        for minmatch in [0.5]:

            os.system(f"{base_folder}/hi_c_data_processing/software/liftOver -minMatch={minmatch} {full_input_path}/regions_bed_file.tsv {base_folder}/hi_c_data_processing/software/{chain_file} {full_input_path}/minmatch{minmatch}_{species_input}_to_{species_output}.bed u")

            os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {full_input_path}/minmatch{minmatch}_{species_input}_to_{species_output}.bed -a {full_target_path}/regions_bed_file.tsv > {full_target_path}/minmatch{minmatch}_{species_input}_to_{species_output}_matched.bed")

            if species_output=='human':

                df_human_mouse_bins = pd.read_csv(f'{full_target_path}/minmatch{minmatch}_{species_input}_to_{species_output}_matched.bed', sep='\t', names=['a', 'b', 'c', 'human_bin', 'a1', 'b1', 'c1', 'mouse_bin', 'overlap'])
            else:
                df_human_mouse_bins = pd.read_csv(f'{full_target_path}/minmatch{minmatch}_{species_input}_to_{species_output}_matched.bed', sep='\t', names=['a', 'b', 'c', 'mouse_bin', 'a1', 'b1', 'c1', 'human_bin', 'overlap'])

        #correct bin_id to correct bin_id

        df_human_mouse_bins['mouse_bin'] = [f"bin_{i}" for i in df_human_mouse_bins['mouse_bin'].tolist()]
        df_human_mouse_bins['human_bin'] = [f"bin_{i}" for i in df_human_mouse_bins['human_bin'].tolist()]


        dk_human = df.copy()
        dk_mouse = df_b.copy()

        df_human_mouse_bins  = df_human_mouse_bins[df_human_mouse_bins['mouse_bin'].isin(dk_mouse.T.index.tolist())]
        df_human_mouse_bins  = df_human_mouse_bins[df_human_mouse_bins['human_bin'].isin(dk_human.T.index.tolist())]
                

        np_of_col = len(cell_type_intersect)*2
        np_of_rows = len(cell_type_intersect)*2
        
        adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))

        
        layer_names = adata.layers.keys()    
        for corr_method in ['pearson']:
                        for given_layer in layer_names:


                                df = adata.to_df(layer=given_layer)

                                df = df.loc[cell_type_intersect,:]

                                df_b = adata_b.to_df(layer=given_layer)

                                df_b = df_b.loc[cell_type_intersect,:]


                                df = df.loc[:,df_human_mouse_bins['human_bin'].tolist()]

                                df = df.T
                                df.index = df_human_mouse_bins['mouse_bin'].tolist()
                                df = df.T
                                df_b = df_b.loc[:,df_human_mouse_bins['mouse_bin'].tolist()]




                                df_corr_real_names = calculate_pearson_correlation(df, df_b, corr_method)

                                l_n = f'{given_layer}_{corr_method}'

                                adata_l.layers[l_n] = df_corr_real_names

                                # Perform cell type intersection
                                #cell_type_intersect = df.index.intersection(df_b.index)

                                hic_cell_type = [x + '_hic' for x in cell_type_intersect]

                                df_corr = df_corr_real_names.loc[cell_type_intersect,:]
                            
                                df_corr = df_corr[hic_cell_type]

                                #df_corr  = df_corr.fillna(0)

                                #df_corr += abs(df_corr.min().min())

                                given_dict = dict(zip(df_corr.index.tolist(), df_corr.index.tolist()))

                                n = len(given_dict.keys())

                                tp_class = np.zeros((n, n))

                                # Fill the diagonal elements with 1
                                np.fill_diagonal(tp_class, 1)

                                df_tp_class = pd.DataFrame(tp_class, index=given_dict.keys(), columns=given_dict.values())

                                for key, value in given_dict.items():
                                    df_tp_class.loc[key, value] = 1
                            
                                df_tp_class = df_tp_class.loc[df_corr.index.tolist(), :]
                                    
                                    
                                df_exp = calculate_auc_nan(df_corr, df_tp_class)

                                adata_l.uns[l_n] = df_exp



        adata_l.obs_names = df_corr_real_names.index.tolist()
        adata_l.var_names = df_corr_real_names.columns.tolist()

        adata_l.write(outputfile_h5ad, compression="gzip")


base_folder = '/grid/gillis/data_norepl/lohia/'
species='human'
resolution='500kbp_raw'
SRP_name='aggregates'
process_type='intra'
ice_type='KR'
input_file_h5ad=f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_by_allbins_max.h5ad'
if species=='mouse':
    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
else:
    gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 
    
    


dist=0
layer_name = 'z_scores'
input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'


marker_name = 'brain_class'
drop_duplicates = True
shuf = False



In [ ]:





for species in ['mouse']:
    for process_type in ['intra']:
        for resolution in ['500kbp_raw', '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
            for shuf in [True, False]:
                for drop_duplicates in [False]:
                    for marker_name in ['brain_class']:
                        for dist in [0,1,10,100]:
                            layer_name = 'z_scores'
                            base_folder = '/grid/gillis/data_norepl/lohia/'
                            SRP_name='aggregates'
                            ice_type='KR'
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                            if species=='mouse':
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                            else:
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 


                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_cross_species.h5ad'

                            if species == 'human':
                                species_b = 'mouse'
                            input_file_h5ad_b = f'{base_folder}/hi_c_data_processing/data_{species_b}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'

                            calc_pair_corr(input_file_h5ad, input_file_h5ad_b, species_b, outputfile_h5ad, resolution, base_folder, SRP_name)





for species in ['mouse']:
    for process_type in ['inter']:
        for resolution in ['500kbp_raw', '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
            for shuf in [True, False]:
                for drop_duplicates in [False]:
                    for marker_name in ['brain_class']:
                            dist = 0
                            layer_name = 'z_scores'
                            base_folder = '/grid/gillis/data_norepl/lohia/'
                            SRP_name='aggregates'
                            ice_type='KR'
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                            if species=='mouse':
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                            else:
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_cross_species.h5ad'

                            if species == 'human':
                                species_b = 'mouse'
                            input_file_h5ad_b = f'{base_folder}/hi_c_data_processing/data_{species_b}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'

                            calc_pair_corr(input_file_h5ad, input_file_h5ad_b, species_b, outputfile_h5ad, resolution, base_folder, SRP_name)







for species in ['human']:
    for process_type in ['intra']:
        for resolution in ['500kbp_raw', '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
            for shuf in [True, False]:
                for drop_duplicates in [False]:
                    for marker_name in ['brain_class']:
                        for dist in [0,1,10,100]:
                            layer_name = 'z_scores'
                            base_folder = '/grid/gillis/data_norepl/lohia/'
                            SRP_name='aggregates'
                            ice_type='KR'
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                            if species=='mouse':
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                            else:
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_cross_species.h5ad'

                            if species == 'human':
                                species_b = 'mouse'
                            input_file_h5ad_b = f'{base_folder}/hi_c_data_processing/data_{species_b}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'

                            calc_pair_corr(input_file_h5ad, input_file_h5ad_b, species_b, outputfile_h5ad, resolution, base_folder, SRP_name)



for species in ['human']:
    for process_type in ['inter']:
        for resolution in ['500kbp_raw', '250kbp_raw', '100kbp_raw', '40kbp_raw', '10kbp_raw']:
            for shuf in [True, False]:
                for drop_duplicates in [False]:
                    for marker_name in ['brain_class']:
                            dist = 0
                            layer_name = 'z_scores'
                            base_folder = '/grid/gillis/data_norepl/lohia/'
                            SRP_name='aggregates'
                            ice_type='KR'
                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{process_type}_{dist}_{layer_name}_by_allbins_max.h5ad'
                            if species=='mouse':
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
                            else:
                                gene_annot_file=f'{base_folder}/hi_c_data_processing/genomes_jlee/gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz' 

                            input_file_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'
                            outputfile_h5ad = f'{base_folder}/hi_c_data_processing/data_{species}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean_cross_species.h5ad'

                            if species == 'human':
                                species_b = 'mouse'
                            input_file_h5ad_b = f'{base_folder}/hi_c_data_processing/data_{species_b}/aggregates/{resolution}/max/hic_gene_{process_type}_{ice_type}_{dist}_{layer_name}_{drop_duplicates}_{shuf}_{marker_name}_by_allbins_max_mean.h5ad'

                            calc_pair_corr(input_file_h5ad, input_file_h5ad_b, species_b, outputfile_h5ad, resolution, base_folder, SRP_name)


In [ ]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc


#egad function

import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck




def calculate_pearson_correlation(df, df_b, corr_method):
    # Perform bin intersection
    bins_intersect = set(df.columns.tolist()).intersection(set(df_b.columns.tolist()))
    df = df.loc[:, bins_intersect]
    #df = df.fillna(0)
    #df_b = df_b.fillna(0)
    df_b = df_b.loc[:, bins_intersect]


    # Z-score normalization
    df_b_z = stats.zscore(df_b, axis=0, nan_policy='omit')
    df_b_z = pd.DataFrame(df_b_z, index=df_b.index.tolist(), columns=df_b.columns)
    df_b_z['cell_type'] = df_b_z.index.tolist()
    df_b_z = df_b_z.set_index(['cell_type'])

    df_z = stats.zscore(df, axis=0, nan_policy='omit')
    df_z = pd.DataFrame(df_z, index=df.index.tolist(), columns=df.columns)
    df_z['cell_type'] = df_z.index.tolist()
    df_z['cell_type'] = [x + '_hic' for x in df_z['cell_type']]
    df_z = df_z.set_index(['cell_type'])
    

    # Concatenate dataframes
    #print (df_b_z)
    #print (df_z)
    df_corr = pd.concat([df_b_z, df_z], axis=0)

    
    
    #df_corr = df_corr.dropna(axis=1, how='all')
    #df_corr = df_corr.dropna(axis=1)
    
    #df_corr = df_corr.set_index(['cell_type'])

            
    features_sc = stats.zscore(df_corr, axis=0, nan_policy='omit')
    
    #features_sc = features_sc.dropna(how='all', axis=1).fillna(0)
    
    #features_sc = features_sc.dropna(how='all', axis=1)
    
                
    df_dist_df = features_sc.T.corr(min_periods=10, method=corr_method)



    return df_dist_df


def calculate_auc_nan(df_dist_df, tp):
    df_jac_subset = df_dist_df.values
    df_exp_subset = tp.values

    coodinates_1 = np.where(np.isnan(df_jac_subset))
    coodinates_2 = np.where(np.isnan(df_exp_subset))

    x_coo = coodinates_1[0].tolist() + coodinates_2[0].tolist()
    y_coo = coodinates_1[1].tolist() + coodinates_2[1].tolist()

    df_jac_subset[x_coo, y_coo] = np.nan
    df_exp_subset[x_coo, y_coo] = np.nan

    predicts2 = bottleneck.nanrankdata(df_jac_subset, axis=1)

    tp = df_exp_subset.copy()
    tn = 1 - tp

    pos_rank_sum = tp * predicts2
    auc_array = (((np.nansum(pos_rank_sum, axis=1) / (np.nansum(tp, axis=1))) - (np.nansum(tp, axis=1) + 1) / 2)) / np.nansum(tn, axis=1)

    df_auc = pd.DataFrame({'cell_type': df_dist_df.index.tolist(), 'AUC': auc_array})

    return df_auc

cell_type_map = {
 'Adipocyte' : 'Adipocytes',
 'Atrial Cardiomyocyte': 'Cardiomyocytes',
 'Ventricular Cardiomyocyte':'Immature_Cardiomyocytes',
 'Endothelial_Arterial': 'Endothelial' ,
 'Fibroblast': 'Fibroblasts',
 'Smooth Muscle': 'Smooth_Muscle_Cells',
 'Lymphocyte': 'Lymphoid_Immune_Cells',
 'Macrophage': 'Myeloid_Immune_Cells',
 'Nervous': 'Neuronal_Cells',}
        

#for each marker-list and input file , I can make one output file

def calc_pair_corr(input_file_h5ad, input_file_another_exp_h5ad, outputfile_h5ad, marker_name):
    

        adata = ad.read_h5ad(f'{input_file_h5ad}', backed='r')
        adata_b = ad.read_h5ad(f'{input_file_another_exp_h5ad}', backed='r')
        df_b = adata_b.to_df()
        
        if marker_name == 'heart':
            df_b.index = [cell_type_map[x] for x in cell_type_map]

        df = adata.to_df()

        cell_type_intersect = df.index.intersection(df_b.index)


        df_b = df_b.loc[cell_type_intersect,:]
        

        np_of_col = len(cell_type_intersect)*2
        np_of_rows = len(cell_type_intersect)*2
        
        adata_l = ad.AnnData(np.zeros((np_of_rows, np_of_col)))

        
        layer_names = adata.layers.keys()    
        for corr_method in ['pearson']:
                        for given_layer in layer_names:
                        #for given_layer in accepted_layer_list:
                        
                        


                                df = adata.to_df(layer=given_layer)

                                df = df.loc[cell_type_intersect,:]

                                df_corr_real_names = calculate_pearson_correlation(df, df_b, corr_method)

                                l_n = f'{given_layer}_{corr_method}'

                                adata_l.layers[l_n] = df_corr_real_names

                                # Perform cell type intersection
                                #cell_type_intersect = df.index.intersection(df_b.index)

                                hic_cell_type = [x + '_hic' for x in cell_type_intersect]

                                df_corr = df_corr_real_names.loc[cell_type_intersect,:]
                            
                                df_corr = df_corr[hic_cell_type]

                                #df_corr  = df_corr.fillna(0)

                                #df_corr += abs(df_corr.min().min())

                                given_dict = dict(zip(df_corr.index.tolist(), df_corr.index.tolist()))

                                n = len(given_dict.keys())

                                tp_class = np.zeros((n, n))

                                # Fill the diagonal elements with 1
                                np.fill_diagonal(tp_class, 1)

                                df_tp_class = pd.DataFrame(tp_class, index=given_dict.keys(), columns=given_dict.values())

                                for key, value in given_dict.items():
                                    df_tp_class.loc[key, value] = 1
                            
                                df_tp_class = df_tp_class.loc[df_corr.index.tolist(), :]
                                    
                                    
                                df_exp = calculate_auc_nan(df_corr, df_tp_class)

                                adata_l.uns[l_n] = df_exp



        adata_l.obs_names = df_corr_real_names.index.tolist()
        adata_l.var_names = df_corr_real_names.columns.tolist()

        adata_l.write(outputfile_h5ad, compression="gzip")


In [1]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py
import os.path
import gc
import os
import matplotlib.pyplot as plt
from pyranges import read_gtf


from umap import UMAP
import plotly.express as px
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
import scipy.spatial as sp, scipy.cluster.hierarchy as hc

import seaborn as sns


import anndata as ad
import scanpy as sc

INFO:numexpr.utils:Note: detected 192 virtual cores but NumExpr set to maximum of 64, check "NUMEXPR_MAX_THREADS" environment variable.
INFO:numexpr.utils:Note: NumExpr detected 192 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.


In [5]:
base_folder = '/grid/gillis/data_norepl/lohia/'
species='mouse'
resolution='1kbp_raw'
SRP_name='aggregates'
input_file_h5ad='/grid/gillis/data_norepl/lohia/hi_c_data_processing/data_mouse/aggregates/1kbp_raw/max/hic_gene_gw_none_by_allbins_max.h5ad'
gene_annot_file='/grid/gillis/data_norepl/lohia/hi_c_data_processing/genomes_jlee/Mus_musculus.GRCm38.94.gtf.gz'
process_type='gw'

In [6]:
    bins_bed = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.csv', names=['chr', 'start', 'end'])
    bins_bed['bin_id'] = bins_bed.index.tolist()

    bins_bed.to_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv', index=False, header=False, sep='\t')
    if species == 'human':

        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Human/hg38-blacklist.v2.bed'
    else:
        blacklist_file = f'{base_folder}/BICCN_enhancer_challenege/10XMultiome/Mouse/mm10-blacklist.v2.bed'

    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {blacklist_file} -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed")
    blacklist_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/all_bin_blacklist.bed', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'c1', 'c2', 'c3', 'c4'])
    

In [9]:
adata = ad.read_h5ad(f'/grid/gillis/data_norepl/lohia/hi_c_data_processing/data_mouse/aggregates/1kbp_raw/max/hic_gene_intra_KR_by_allbins_max.h5ad')



In [4]:
    data = adata.X + 0.0
    
    if resolution == '1kbp_raw':
    
        data = data.astype('float32')
        
    elif resolution == '10kbp_raw':
    
        data = data.astype('float32')
    else:
        data = data.astype('float64')

        
    
    nan_columns = blacklist_bins['bin_id'].tolist()

    data[:, nan_columns] = np.nan


    chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()

    chrom_index_list  = {}
    for chrom in chr_list:
          st = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[0]
          en = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[-1]
          chrom_index_list[chrom] = list(range(st, en+1))

    chrom_index_list_intra = {}
    for chrom in chr_list:
        index_list = []
        for chrom2 in chr_list:
            if chrom2 != chrom:
                index_list.extend(chrom_index_list[chrom2])

        chrom_index_list_intra[chrom] = index_list

    gtf = read_gtf(gene_annot_file)
    genes = gtf.df.loc[gtf.df['Feature'] == 'gene'].copy()
    genes['gene_id'] = [x.split('.')[0] for x in genes['gene_id']]
    genes['gene_id'].drop_duplicates(inplace=True)

    if not genes['Chromosome'].str.startswith('chr').any():
        genes['Chromosome'] = [f'chr{x}' for x in genes['Chromosome']]

    genes  = genes.set_index('gene_id')

    genes = genes.loc[adata.obs_names.tolist(), :]
    
    genes = genes.reset_index()



    genes[['Chromosome', 'Start', 'End', 'gene_id']].to_csv(f'{base_folder}hi_c_data_processing/data_{species}/gene_info.tsv', index=False, header=False, sep='\t')


    os.system(f"~/.conda/envs/hicexplorer/bin/bedtools intersect -wo -b {base_folder}hi_c_data_processing/data_{species}/gene_info.tsv -a {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/regions_bed_file.tsv > {base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv")
    gene_id_bins = pd.read_csv(f'{base_folder}/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/gene_info_bin_id.tsv', sep='\t', names=['d', 'd1', 'd2', 'bin_id', 'c', 'st', 'end', 'gene_id', 'c4'])

    


NameError: name 'adata' is not defined

In [14]:
    if process_type == 'intra':

        layer_value_list = [0, 1, 10, 100, 1000]
        layer_name_list = ['intra']*len(layer_value_list)

    if process_type == 'inter':
        layer_name_list = ['inter']
        layer_value_list = [0]

    if process_type == 'gw':
        layer_value_list = [0, 1, 10, 100, 1000]
        layer_name_list = ['intra']*len(layer_value_list)
        layer_name_list.append('inter')
        layer_value_list.append(0)



    for layer_type, dist in zip(layer_name_list, layer_value_list):
        
        new_layer_name = f'{process_type}_{layer_type}_{dist}'
        
        if new_layer_name in adata.layers:
            continue
        else:

            mask = np.zeros_like(data, dtype=bool)

        

            for index, row in genes.iterrows():

                if layer_type == 'intra':
                    columns_to_mask = chrom_index_list_intra[row['Chromosome']]
                else:
                    columns_to_mask = chrom_index_list[row['Chromosome']]

                mask[index, columns_to_mask] = True

                if layer_type == 'intra':

                    start_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].min()

                    end_index = gene_id_bins[gene_id_bins['gene_id'] == row['gene_id']]['bin_id'].max()

                    mask[index, start_index:end_index+1]  = True

                    #for idx in [start_index, end_index]:
                    mask[index, max(0, start_index - dist):min(data.shape[1], end_index + dist+1)] = True




            data_layered = np.where(mask, np.nan, data)



            layer_name = f'{process_type}_{layer_type}_{dist}'

            adata.layers[layer_name] = data_layered

            z_scores = stats.zscore(data_layered, axis=1, nan_policy='omit')


            clipped_z_scores = np.clip(z_scores, -10, 10)



            layer_name = f'{process_type}_{layer_type}_{dist}_z_scores'

            adata.layers[layer_name] = clipped_z_scores



            del z_scores
            del clipped_z_scores
            gc.collect()

            #data_plus_one = data_layered + 1

            #log_transformed_data = np.log1p(data_plus_one)

            del data_layered
            #del data_plus_one
            gc.collect()

            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed'

            #adata.layers[layer_name] = log_transformed_data

            #z_scores = stats.zscore(log_transformed_data, axis=1, nan_policy='omit')

            #clipped_z_scores = np.clip(z_scores, -10, 10)



            #layer_name = f'{process_type}_{layer_type}_{dist}_log_transformed_z_scores'

            #adata.layers[layer_name] = clipped_z_scores

            #del z_scores
            #del log_transformed_data
            #del clipped_z_scores
            #gc.collect()

            adata.write(f'{input_file_h5ad}', compression="gzip")

RuntimeError: Can't get creation plist (bad object header version number)

Above error raised while writing key 'gw_intra_0' of <class 'h5py._hl.group.Group'> to /

In [ ]:
if [[ "$species" == "human" ]]
then
CHROMS=/grid/gillis/data_norepl/nfox/genomes/homo_sapiens_38/hg38.chrom.sizes 
chrom_list="chr1,chr2,chr3,chr4,chr5,chr6,chr7,chr8,chr9,chr10,chr11,chr12,chr13,chr14,chr15,chr16,chr17,chr18,chr19,chr20,chr21,chr22"
chrom_list_2="chr1 chr2 chr3 chr4 chr5 chr6 chr7 chr8 chr9 chr10 chr11 chr12 chr13 chr14 chr15 chr16 chr17 chr18 chr19 chr20 chr21 chr22"
GENOME="gencode.v28.chr_patch_hapl_scaff.annotation.gtf.gz"
EXP_NETWORKS="human_prioAggNet.hdf5"

elif [[ "$species" == "mouse" ]]
then
CHROMS=/grid/gillis/data_norepl/nfox/genomes/mus_musculus_10/mm10.chrom.sizes
GENOME="Mus_musculus.GRCm38.94.gtf.gz"
EXP_NETWORKS="mouse_prioAggNet.hdf5"
chrom_list="chr1,chr2,chr3,chr4,chr5,chr6,chr7,chr8,chr9,chr10,chr11,chr12,chr13,chr14,chr15,chr16,chr17,chr18,chr19"
chrom_list_2="chr1 chr2 chr3 chr4 chr5 chr6 chr7 chr8 chr9 chr10 chr11 chr12 chr13 chr14 chr15 chr16 chr17 chr18 chr19"


In [ ]:
add_layers_anndata(process_type, input_file_h5ad, gene_annot_file, species, SRP_name, resolution, base_folder)



In [ ]:

ice_type='none'

base_path='/grid/gillis/data_norepl/lohia/'


        
    python ${software_path}/add_contact_norm_layers.py \
    --process_type ${process} \
    --species ${species} \
    --input_file_h5ad /grid/gillis/data_norepl/lohia/hi_c_data_processing/data_mouse/aggregates/10kbp_raw/max/hic_gene_gw_none_by_allbins_max.h5ad \
    --base_path $base_path \
    --resolution $NETWORK \
    --SRP $SRP_name \
    --gene_annot_file ${base_folder}/lohia/hi_c_data_processing/genomes_jlee/${GENOME}
    

